In [1]:
import random 
import gym
import numpy as np 
from collections import deque
import tensorflow as tf 
import tflearn as tl 
from tflearn.activations import softmax

Instructions for updating:
Colocations handled automatically by placer.


In [2]:
episode_infos = {'run' : [], 'step' : [], 'total_reward' : [], 'avg_reward' : []}

In [3]:
def cartpole():
    env = gym.make('CartPole-v1')
    observation_space = env.observation_space.shape[0]
    action_space = env.action_space.n
    sess = tf.InteractiveSession()
    a3c_solver = A3CSolver(observation_space, action_space, sess)
    sess.run(tf.global_variables_initializer())
    #a3c_solver.model.load_weights('dqn_weights_%i.h5' % (prev_stop))
    run = 0
    while True:
    #for _ in range(300):
        run += 1
        state = env.reset()
        state = np.reshape(state, [1, observation_space])
        step = 0
        total_reward = 0
        while True:
            step += 1
            action = a3c_solver.act(state)
            state_next, reward, terminal, info = env.step(action)
            reward = reward if not terminal else -reward
            total_reward += reward
            state_next = np.reshape(state_next, [1, observation_space])
            a3c_solver.remember(state, action, reward, state_next, terminal)
            state = state_next
            if terminal:
                
                episode_infos['run'].append(run)
                episode_infos['step'].append(step)
                episode_infos['total_reward'].append(total_reward)
                episode_infos['avg_reward'].append(total_reward / step)
                
                print('epsilon : ' + str(a3c_solver.exploration_rate))
                print('run : ' + str(run) + ' score : ' + str(total_reward) + ' avg_score : ' + str(total_reward / step))
                break
            a3c_solver.experience_replay()
        #dqn_solver.model.save_weights('dqn_weights_%i.h5' % (run))

### Loss function : 
$$L= L_\pi + \alpha L_Q + \beta L_{reg}$$
### Policy loss :
$$A = (R - Q_{a_i\sim \pi}(a_i,s_i; \theta'_q))$$
$$\frac{\partial\,J(\pi)}{\partial\, \theta'} = \frac{1}{n}\sum_{i=1}^{n}\frac{\partial\,log\,\pi (a_i|s_i;\theta')}{\partial\,\theta'}\; A$$
$$\therefore J(\pi) = \frac{1}{n}\sum_{i=1}^{n}log\,\pi (a_i|s_i;\theta')\; A\;\;\;\;\;\;[\because A\;is\;considered\;constant]$$
∵ We want to maximize 𝐽(𝜋) $$L_\pi = -J(\pi)$$
### Value loss :
$$J(Q) = \sum_{i=1}^{n}(R - Q_{a_i\sim \pi}(a_i,s_i; \theta'_q))$$
$$L_Q = J(Q)$$
### Policy entropy :
$$H(\overrightarrow{\pi(s)})=-\sum_{i=1}^{n}\sum_{k=1}^{m} \pi(s_i)_k\cdot log\, \pi(s_i)_k$$
$$L_{reg}=H(\overrightarrow{\pi(s)})$$

In [4]:
y = 0.95
l_rate = 0.0001

exp_memory_size = 1000000
batch_size = 20

exploration_max = 1.0
exploration_min = 0.01
exploration_decay = 0.9995

alpha = 0.5
beta = 0.01

In [5]:
class A3CSolver():
    def __init__(self, observation_space, action_space, sess):
        self.sess = sess
        self.exploration_rate = exploration_max
        self.action_space = action_space
        self.memory = deque(maxlen = exp_memory_size)
        
        self.state = tl.input_data(shape = [None, observation_space], name = 'S_i')
        self.action = tl.input_data(shape = [None, action_space], name = 'A_i')
        self.R = tl.input_data(shape = [None, 1], name = 'R_i')
        
        #Actor 𝜋(a_i|s_i;𝜃′)
        self.actor = self.build_actor(self.state, action_space)
        #Critic Q_a_i∼𝜋(a_i,s_i;𝜃′_q)
        self.critic = self.build_critic(self.state, self.action)
        
        #Loss L
        self.loss = self.compute_loss()
        #Optimize ops 
        self.opt = tf.train.AdamOptimizer(learning_rate = l_rate).minimize(self.loss)
        
    def build_actor(self, state_input, action_space):
        #State input s_i
        a_h1 = tl.fully_connected(state_input, 24)        
        a_h2 = tl.fully_connected(a_h1, 48)        
        a_logit = tl.fully_connected(a_h2, action_space)
        return softmax(a_logit)
    
    def build_critic(self, state_input, action_input):
        #Action input a_i
        as_h1 = tl.fully_connected(action_input, 24)
        as_h2 = tl.fully_connected(as_h1, 48)
        #State input s_i
        ss_h1 = tl.fully_connected(state_input, 24)
        ss_h2 = tl.fully_connected(ss_h1, 48)
        #Combine state action input 
        q_h1 = tl.layers.merge_ops.merge([as_h2, ss_h2], mode = 'elemwise_sum')
        return tl.fully_connected(q_h1, 1)
    
    def remember(self, state, action, reward, state_next, done):
        self.memory.append([state, action, reward, state_next, done])
        
    def act(self, state, infer = False):
        #act
        if not infer and np.random.rand() < self.exploration_rate:
            return random.randrange(self.action_space)
        action = self.sess.run(self.actor, feed_dict = {self.state : state})
        return np.argmax(action[0])
    
    def experience_replay(self):
        if len(self.memory) < batch_size:
            return
        batch = random.sample(self.memory, batch_size)
        for state, action, reward, state_next, done in batch:
            R = np.array(reward).reshape([1, 1])
            action = np.identity(2)[action].reshape([1, self.action_space])
            if not done:
                action_next = self.sess.run(self.actor, feed_dict = {self.state : state_next})
                R = reward + y * self.sess.run(self.critic, feed_dict = {self.state : state_next, self.action : action_next})
            #Optimize
            loss, _, a, b, c= self.sess.run([self.loss, self.opt, self.L_pi, self.L_v, self.actor], feed_dict = {self.state : state, 
                                                                        self.action : action, 
                                                                        self.R : R})
            print(loss, a, b, c)
            self.exploration_rate *= exploration_decay
            self.exploration_rate = max(exploration_min, self.exploration_rate)

    def compute_loss(self):
        #Advantage
        A = self.R - self.critic
        #Policy loss 
        self.L_pi = - tf.reduce_mean(tf.reduce_mean(tf.log(self.actor + 1e-13) * tf.stop_gradient(A), axis = -1))
        #Value loss
        self.L_v = tf.reduce_mean(tf.math.square(A))
        #Policy entropy 
        self.L_reg = tf.reduce_mean(tf.reduce_sum(tf.multiply(self.actor, tf.log(self.actor + 1e-13)), axis = -1))
        #Total loss 
        return self.L_pi + alpha * self.L_v #+ beta * self.L_reg 

In [ ]:
cartpole()

Instructions for updating:
Use tf.cast instead.
1.1930141 0.6930927 0.9998429 [[0.4999991 0.5000009]]
1.192955 0.6930685 0.9997729 [[0.5000768 0.4999232]]
1.1933331 0.69322336 1.0002196 [[0.49998417 0.5000158 ]]
1.1933211 0.69321835 1.0002055 [[0.4999583 0.5000417]]
1.1928258 0.6930156 0.9996204 [[0.49995357 0.50004643]]
1.1927974 0.693004 0.9995869 [[0.49992642 0.50007355]]
1.1927724 0.69299376 0.9995572 [[0.4999226  0.50007737]]
1.192745 0.6929825 0.999525 [[0.50004315 0.49995688]]
1.1927162 0.69297075 0.99949104 [[0.50011295 0.49988705]]
1.1926814 0.69295645 0.9994499 [[0.499962 0.500038]]
1.1931956 0.693167 1.0000572 [[0.50007874 0.4999213 ]]
1.193172 0.6931573 1.0000293 [[0.5000327 0.4999673]]
1.1931419 0.69314504 0.9999938 [[0.500022 0.499978]]
1.1931088 0.69313145 0.9999546 [[0.50004566 0.49995437]]
1.1925831 0.6929162 0.99933374 [[0.5000525  0.49994752]]
1.1925664 0.69290936 0.99931395 [[0.5000303  0.49996975]]
1.1930087 0.69309044 0.9998363 [[0.49992922 0.5000708 ]]
1.1925184 

1.187086 0.6906632 0.9928456 [[0.49999973 0.5000003 ]]
1.1786577 0.6872003 0.9829146 [[0.5000035 0.4999965]]
1.1865097 0.69042677 0.9921659 [[0.50000274 0.49999726]]
1.1859968 0.6902163 0.99156106 [[0.5000068  0.49999318]]
1.1861837 0.69029295 0.9917815 [[0.50000274 0.4999973 ]]
1.1765715 0.68634164 0.98045963 [[0.50000674 0.49999323]]
1.1776955 0.68680435 0.98178226 [[0.50000185 0.49999818]]
1.1853745 0.68996084 0.99082726 [[0.5000192  0.49998078]]
1.1857938 0.6901329 0.9913216 [[0.49999315 0.50000685]]
1.1770542 0.68654037 0.9810276 [[0.4999826 0.5000174]]
1.1856487 0.6900734 0.9911505 [[0.4999826 0.5000174]]
1.1760812 0.6861397 0.9798829 [[0.49998322 0.50001675]]
1.1853698 0.68995893 0.9908218 [[0.499996 0.500004]]
1.1857263 0.6901052 0.9912421 [[0.50000954 0.4999905 ]]
1.1757079 0.685986 0.97944397 [[0.50000983 0.4999902 ]]
1.1749535 0.68567514 0.9785565 [[0.50000453 0.49999547]]
1.1848943 0.6897637 0.9902613 [[0.5000097 0.4999903]]
1.1739521 0.68526256 0.97737914 [[0.50001603 0.49

1.1552576 0.6775319 0.9554514 [[0.5000003  0.49999973]]
1.110437 0.6587839 0.90330625 [[0.5000126 0.4999874]]
1.1548486 0.6773622 0.9549728 [[0.5000256 0.4999744]]
1.1592218 0.6791755 0.9600925 [[0.5000285 0.4999715]]
1.1109405 0.65899616 0.90388846 [[0.50001544 0.4999846 ]]
1.15589 0.6777943 0.95619136 [[0.50001407 0.4999859 ]]
1.1096468 0.6584506 0.9023924 [[0.50000334 0.49999666]]
1.1531199 0.6766446 0.9529506 [[0.4999874  0.50001264]]
1.1528667 0.67653954 0.9526544 [[0.4999831  0.50001687]]
1.1458671 0.67362916 0.9444758 [[0.49999115 0.5000089 ]]
1.1103469 0.6587459 0.9032021 [[0.49998495 0.5000151 ]]
1.1015763 0.6550409 0.8930708 [[0.5000136 0.4999864]]
0.57481503 -1.3654265 3.8804832 [[0.50002563 0.49997437]]
1.1530164 0.67660165 0.95282954 [[0.49999964 0.50000036]]
1.0960493 0.6526999 0.88669896 [[0.50004    0.49996004]]
1.1063989 0.65707964 0.8986386 [[0.5000162  0.49998376]]
1.1423159 0.6721498 0.94033206 [[0.50003076 0.49996927]]
1.1500536 0.67537075 0.9493657 [[0.49999586 0.

1.1047794 0.6563954 0.896768 [[0.49999827 0.5000017 ]]
0.9567331 0.5920048 0.72945666 [[0.5000077  0.49999228]]
0.9547858 0.59113204 0.7273075 [[0.5000201 0.4999799]]
1.1145948 0.66053605 0.9081176 [[0.50003946 0.49996054]]
0.9639113 0.59521574 0.7373911 [[0.50002795 0.49997208]]
1.0978864 0.6534786 0.8888157 [[0.49999633 0.50000364]]
1.0978087 0.6534456 0.8887263 [[0.49998575 0.50001425]]
0.945413 0.5869214 0.7169832 [[0.49997213 0.5000279 ]]
1.0898844 0.65008295 0.87960285 [[0.49999103 0.50000894]]
0.9492818 0.58866143 0.7212407 [[0.49998719 0.5000128 ]]
0.9427637 0.5857282 0.714071 [[0.4999855  0.50001454]]
1.101335 0.6549388 0.89279234 [[0.50000346 0.49999654]]
0.9420773 0.5854188 0.71331686 [[0.5000045  0.49999553]]
0.954034 0.5907949 0.72647816 [[0.50002563 0.49997434]]
1.1009264 0.65476584 0.89232117 [[0.50001615 0.49998388]]
0.94396806 0.5862708 0.71539444 [[0.50000304 0.49999693]]
1.1109645 0.65900636 0.9039165 [[0.5000103  0.49998966]]
1.0999122 0.6543365 0.8911513 [[0.499996

0.74283016 0.49146527 0.50272983 [[0.49984333 0.5001567 ]]
0.7386378 0.4893906 0.49849436 [[0.49985242 0.5001476 ]]
0.75200546 0.49599043 0.5120301 [[0.49984267 0.5001573 ]]
1.0031976 0.6126223 0.7811505 [[0.49991357 0.5000864 ]]
1.0036662 0.61282825 0.78167576 [[0.49995646 0.5000435 ]]
0.7234208 0.48182267 0.48319626 [[0.50003296 0.49996707]]
0.7203649 0.48029572 0.48013842 [[0.50011027 0.49988967]]
0.98882055 0.6062846 0.76507187 [[0.50009334 0.49990666]]
0.7393224 0.4897297 0.49918544 [[0.5001477  0.49985233]]
0.98253024 0.6035001 0.75806016 [[0.5001379  0.49986207]]
0.97470784 0.6000273 0.749361 [[0.50010103 0.49989897]]
0.71967566 0.47995093 0.47944942 [[0.50002706 0.49997297]]
0.9962704 0.6095733 0.7733943 [[0.49999127 0.50000876]]
0.722671 0.48144823 0.48244545 [[0.4999362 0.5000638]]
1.0060378 0.61387 0.7843357 [[0.49992856 0.5000714 ]]
0.68556225 0.46273097 0.4456626 [[0.49989203 0.50010794]]
0.9933177 0.60827106 0.7700934 [[0.49991208 0.5000879 ]]
0.9711174 0.59842956 0.74537

...

0.33655292 0.32808354 0.016938733 [[0.0065053 0.9934947]]
0.82784086 0.80802417 0.039633412 [[2.9835498e-04 9.9970156e-01]]
0.40690607 0.36633518 0.08114176 [[0.08331743 0.91668254]]
3.57301 3.5286658 0.088688284 [[1.0000000e+00 5.0972945e-11]]
1.5486706 1.4374113 0.22251861 [[0.9977393  0.00226067]]
-0.057201635 -0.05850095 0.0025986293 [[0.11365964 0.8863404 ]]
0.44301566 0.3363554 0.21332055 [[0.36980528 0.6301947 ]]
0.41026372 0.31407097 0.1923855 [[0.3942089  0.60579115]]
0.39186722 0.32518274 0.13336898 [[0.21450566 0.7854943 ]]
0.47660208 0.46377203 0.025660107 [[0.00306629 0.9969337 ]]
0.43479818 0.3399647 0.18966702 [[0.29969266 0.70030737]]
0.0022711204 0.0022675502 7.1406284e-06 [[0.75844526 0.24155472]]
2.4078035 2.363366 0.088875264 [[9.9999988e-01 1.3007482e-07]]
0.047215212 0.04591648 0.0025974629 [[0.7915652  0.20843485]]
-0.005686972 -0.005710402 4.6860518e-05 [[0.74788386 0.25211617]]
3.3438847 3.2328467 0.22207616 [[9.9999893e-01 1.0998727e-06]]
0.016815536 0.0166006

0.29169205 0.28399122 0.01540169 [[0.01039708 0.989603  ]]
0.2981689 0.2849592 0.026419394 [[0.03096611 0.96903396]]
-0.037566423 -0.03863928 0.0021457155 [[0.25214565 0.74785435]]
-0.028561058 -0.028920284 0.00071845285 [[0.8666519  0.13334808]]
-0.022171706 -0.022687668 0.0010319235 [[0.58045113 0.4195489 ]]
0.38742778 0.36106992 0.0527157 [[0.9549095  0.04509053]]
1.4580758 1.4520926 0.0119662285 [[2.8510874e-12 1.0000000e+00]]
3.2038088 3.1179159 0.17178594 [[9.9999976e-01 2.9235673e-07]]
0.3451691 0.31811744 0.054103304 [[0.06973761 0.93026245]]
0.29148838 0.28181913 0.019338485 [[0.01768075 0.9823193 ]]
0.33727905 0.31595004 0.042658027 [[0.0493471 0.9506529]]
0.3172836 0.25149983 0.13156754 [[0.4895129 0.5104871]]
0.031045958 0.030888854 0.00031420912 [[0.0316507  0.96834934]]
0.3086102 0.30426416 0.008692057 [[0.00146541 0.99853456]]
0.32646653 0.28442457 0.08408394 [[0.16926463 0.8307354 ]]
0.23564948 0.22773317 0.015832633 [[0.972452   0.02754801]]
-0.059458055 -0.06067392 0.

0.37770104 0.32320762 0.108986825 [[0.1700498 0.8299502]]
0.43756726 0.33037645 0.21438164 [[0.40005553 0.5999445 ]]
0.13785996 0.13100702 0.013705878 [[0.87859535 0.12140464]]
0.1036379 0.09887995 0.009515893 [[0.8439573  0.15604274]]
0.676305 0.664963 0.022683937 [[1.4627709e-04 9.9985373e-01]]
-0.02226611 -0.022694733 0.0008572455 [[0.3055633 0.6944367]]
0.11220427 0.10690157 0.0106053995 [[0.8529631  0.14703687]]
0.4195798 0.3824691 0.074221455 [[0.06449957 0.93550044]]
0.4345383 0.38486823 0.099340126 [[0.09623033 0.90376973]]
2.2689378 2.1598625 0.21815047 [[9.999038e-01 9.625136e-05]]
0.35706177 0.28523415 0.14365524 [[0.3326408  0.66735923]]
0.9810591 0.9520668 0.057984594 [[3.6809628e-04 9.9963188e-01]]
0.41656265 0.3804665 0.072192326 [[0.06284101 0.93715906]]
0.40376225 0.31643882 0.17464685 [[0.32662487 0.67337507]]
0.38274658 0.32512408 0.115245 [[0.17949618 0.82050383]]
0.45338827 0.37408915 0.15859821 [[0.18821414 0.8117859 ]]
0.07826287 0.07510629 0.006313157 [[0.814655

-0.080113575 -0.08138952 0.0025518793 [[0.04159249 0.95840746]]
0.0060765175 0.00603857 7.589572e-05 [[0.5000652  0.49993476]]
0.13860385 0.1316814 0.013844896 [[0.87862325 0.12137675]]
0.43165562 0.347486 0.16833925 [[0.24272723 0.7572728 ]]
0.16880521 0.16010718 0.017396057 [[0.902207   0.09779295]]
0.3852423 0.36063352 0.049217597 [[0.04035879 0.9596412 ]]
0.4108693 0.34055823 0.14062214 [[0.7955984  0.20440164]]
0.40025377 0.30527818 0.18995121 [[0.43980882 0.5601912 ]]
0.029781988 0.029667528 0.0002289182 [[0.02021667 0.97978336]]
-0.042978615 -0.04408065 0.002204066 [[0.18841593 0.81158406]]
-0.07698753 -0.07839453 0.0028140033 [[0.05507828 0.94492173]]
-0.06500773 -0.06960134 0.009187221 [[0.37363562 0.6263644 ]]
1.0502679 1.0391809 0.02217406 [[8.6788577e-07 9.9999917e-01]]
0.2380018 0.22475766 0.026488263 [[0.9322411  0.06775897]]
0.42082247 0.40876132 0.024122281 [[0.00520322 0.9947968 ]]
0.6180521 0.50423974 0.22762476 [[0.85946906 0.14053094]]
0.25702992 0.24190953 0.030240

0.8594776 0.8245699 0.06981536 [[0.998049   0.00195094]]
0.059516825 0.057112694 0.0048082657 [[0.7396408 0.2603592]]
0.38629937 0.37346044 0.02567783 [[0.00954648 0.9904535 ]]
0.13234074 0.12430519 0.016071122 [[0.8305967  0.16940331]]
0.019659992 0.019566976 0.0001860346 [[0.06039314 0.93960685]]
0.18253483 0.17192468 0.021220285 [[0.8944885  0.10551155]]
0.31510854 0.25098974 0.12823762 [[0.4380299 0.5619701]]
0.32240063 0.29690102 0.050999224 [[0.07824213 0.9217579 ]]
0.3290799 0.2595573 0.13904516 [[0.46180266 0.53819734]]
3.0501127 2.9793503 0.14152479 [[9.9999988e-01 1.3215697e-07]]
0.36818963 0.3224732 0.09143285 [[0.13735966 0.8626403 ]]
0.13622671 0.1361562 0.00014101925 [[1.0981916e-10 1.0000000e+00]]
0.07774286 0.07395057 0.0075845877 [[0.7588422 0.2411578]]
0.34263346 0.29832765 0.08861162 [[0.16050774 0.83949226]]
0.3421607 0.32397863 0.036364146 [[0.03464386 0.9653562 ]]
0.018901791 0.018782653 0.00023827542 [[0.09716181 0.9028382 ]]
0.016028548 0.015866073 0.00032494936